## Combining all downstream used A2TEA data into one RDS object
## Also performing necessary data manipulation

In [86]:
#if (!requireNamespace("BiocManager", quietly = TRUE))
#    install.packages("BiocManager")

#BiocManager::install("DESeq2")


#lfcShrinkage isn't installable at the moment - problem for later
#install.packages("mvtnorm")
#BiocManager::install("apeglm")

install.packages("data.table")

Updating HTML index of packages in '.Library'

Making 'packages.html' ...
 done



In [1]:
library(DESeq2)
#library(apeglm)
library(BiocGenerics)
library(tidyverse)
library(data.table)

Loading required package: S4Vectors

Loading required package: stats4

Loading required package: BiocGenerics

Loading required package: parallel


Attaching package: ‘BiocGenerics’


The following objects are masked from ‘package:parallel’:

    clusterApply, clusterApplyLB, clusterCall, clusterEvalQ,
    clusterExport, clusterMap, parApply, parCapply, parLapply,
    parLapplyLB, parRapply, parSapply, parSapplyLB


The following objects are masked from ‘package:stats’:

    IQR, mad, sd, var, xtabs


The following objects are masked from ‘package:base’:

    anyDuplicated, append, as.data.frame, basename, cbind, colnames,
    dirname, do.call, duplicated, eval, evalq, Filter, Find, get, grep,
    grepl, intersect, is.unsorted, lapply, Map, mapply, match, mget,
    order, paste, pmax, pmax.int, pmin, pmin.int, Position, rank,
    rbind, Reduce, rownames, sapply, setdiff, sort, table, tapply,
    union, unique, unsplit, which, which.max, which.min



Attaching package: ‘S4Vectors’


The

#### Find all DESeq2 differential expression RDS objects and load them
##### Names are given based on the species/ecotype/etc. name

In [2]:
dea_list <- list.files(path = "R/deseq2/dea_final/", pattern = "dea_*", full.names=TRUE)
dea_list_short <- list.files(path = "R/deseq2/dea_final/", pattern = "dea_*", full.names=FALSE)

#species <- str_sub(dea_list_short[[1]], start=5)

#lapply(dea_list_short, str_sub(start=5))


listRDS <- lapply(dea_list, readRDS, .GlobalEnv)


for (i in 1:length(listRDS)){
    assign(str_sub(dea_list_short[[i]], start=5), listRDS[[i]])
}

#remove unused combined list object
rm(listRDS)

In [4]:
#nice for later - but needs install of package "apeglm"

#link on logFC shrinking
#https://support.bioconductor.org/p/77461/
#?lfcShrink
#lfcShrink(arabidopsis_dea, coef=2, type="apeglm")
#resultsNames(arabidopsis_dea)

Formal class 'DESeqDataSet' [package "DESeq2"] with 8 slots
  ..@ design            :Class 'formula'  language ~condition
  .. .. ..- attr(*, ".Environment")=<environment: R_GlobalEnv> 
  ..@ dispersionFunction:function (q)  
  .. ..- attr(*, "coefficients")= Named num [1:2] 0.0156 2.5109
  .. .. ..- attr(*, "names")= chr [1:2] "asymptDisp" "extraPois"
  .. ..- attr(*, "fitType")= chr "parametric"
  .. ..- attr(*, "varLogDispEsts")= num 1.11
  .. ..- attr(*, "dispPriorVar")= num 0.621
  ..@ rowRanges         :Formal class 'CompressedGRangesList' [package "GenomicRanges"] with 5 slots
  .. .. ..@ unlistData     :Formal class 'GRanges' [package "GenomicRanges"] with 7 slots
  .. .. .. .. ..@ seqnames       :Formal class 'Rle' [package "S4Vectors"] with 4 slots
  .. .. .. .. .. .. ..@ values         : Factor w/ 0 levels: 
  .. .. .. .. .. .. ..@ lengths        : int(0) 
  .. .. .. .. .. .. ..@ elementMetadata: NULL
  .. .. .. .. .. .. ..@ metadata       : list()
  .. .. .. .. ..@ ranges  

In [3]:
species_list <- vector()

for (i in 1:length(dea_list_short)){
    species_list <- c(species_list, str_sub(dea_list_short[[i]], start=5))
}

list_AllSpeciesDEResultsDataFrames <- list()

for (i in species_list) {
    # individual species file could be deleted but perhaps I'll need them later; kept for now...
    assign(paste0(i, "_DEresultsTable"), as.data.frame(results(get(i))))
    # create gene name vector here (when list is constructed rownames become unique species-gene combination)
    gene <- rownames(get(paste0(i, "_DEresultsTable")))
    df_with_genes <- add_column(get(paste0(i, "_DEresultsTable")), gene, .before = "baseMean")
    # also add a species column which will will also come in handy during the shiny steps
    species <- replicate(nrow(df_with_genes), i)
    df_with_genes <- add_column(df_with_genes, species, .before = "gene")
    #create list of dataframes, which will come in handy
    list_AllSpeciesDEResultsDataFrames[[i]] <- df_with_genes
    #list_AllSpeciesDEResultsDataFrames[[i]] <- (get(paste0(i, "_DEresultsTable")))
}

#str(list_AllSpeciesDEResultsDataFrames)

#create combined "mega" dataframe of all species, which is going  to be used for shiny lookup

combined_AllSpeciesDEResultsDataFrames <- do.call("rbind", list_AllSpeciesDEResultsDataFrames)


#str(combined_AllSpeciesDEResultsDataFrames)
#head(combined_AllSpeciesDEResultsDataFrames)
#head(list_AllSpeciesDEResultsDataFrames[[1]])
#?rbind

### creating long format HOG-genes relation table

In [4]:
HOG_file_raw <- read_delim("orthofinder/final-results/Phylogenetic_Hierarchical_Orthogroups/N0.tsv", delim = "\t")

#drop the OG, Gene Tree Parent Clade
HOG_file_short <- HOG_file_raw %>% select (-c(OG, `Gene Tree Parent Clade`)) 


#merge all species columns into one and remove the solo ones
#use all colnames except first - thus all species
HOG_file_merged <- HOG_file_short %>% unite(x,
                                          c(colnames(HOG_file_short)[-1]),
                                          sep = ",", 
                                          na.rm = TRUE,
                                          remove = TRUE)

#transform into long format - each row 1 gene and it's corresponding HOG in seperate columns
HOG_file_long <- HOG_file_merged %>%
                    mutate(unpacked = str_split(x, ",")) %>%
                    unnest(cols = c(unpacked)) %>%
                    mutate(genes = str_trim(unpacked)) %>% 
                    select(-c(x, unpacked)) %>% 
                    rename(gene = genes)

str(HOG_file_long)

Parsed with column specification:
cols(
  HOG = col_character(),
  OG = col_character(),
  `Gene Tree Parent Clade` = col_character(),
  Arabidopsis_thaliana = col_character(),
  Hordeum_vulgare = col_character(),
  Zea_mays = col_character()
)



tibble [90,454 × 2] (S3: tbl_df/tbl/data.frame)
 $ HOG : chr [1:90454] "N0.HOG0000000" "N0.HOG0000000" "N0.HOG0000000" "N0.HOG0000000" ...
 $ gene: chr [1:90454] "Zm00001d020494" "Zm00001d007563" "Zm00001d052359" "Zm00001d037178" ...


### adding specific HOG or singleton info as HOG column to DE tables

In [38]:
#?full_join
HOG_DE.a2tea <- full_join(combined_AllSpeciesDEResultsDataFrames, HOG_file_long, 
              by = c("gene")) %>% 
                replace_na(list(HOG = "singleton"))

HOG_DE.a2tea

species              gene            baseMean    log2FoldChange
1      Arabidopsis_thaliana AT1G01010         41.195470 -0.14217239   
2      Arabidopsis_thaliana AT1G01020        248.824248  0.04827472   
3      Arabidopsis_thaliana AT1G01030         98.557671  0.15532807   
4      Arabidopsis_thaliana AT1G01040        349.289858  0.15787058   
5      Arabidopsis_thaliana AT1G01050        490.887038 -0.01060098   
6      Arabidopsis_thaliana AT1G01060        504.758668 -0.18656451   
7      Arabidopsis_thaliana AT1G01070          3.147454 -2.34442042   
8      Arabidopsis_thaliana AT1G01080       1092.806741 -0.10177468   
9      Arabidopsis_thaliana AT1G01090       2113.288680 -0.15603571   
10     Arabidopsis_thaliana AT1G01100       7878.920882 -0.09447338   
11     Arabidopsis_thaliana AT1G01110         41.415271  0.28316520   
12     Arabidopsis_thaliana AT1G01120        206.115599  0.21593642   
13     Arabidopsis_thaliana AT1G01130         23.419327 -0.31815146   
14     Arabidopsis_thaliana AT1G01140        127.526402 -0.06462070   
15     Arabidopsis_thaliana AT1G01150          9.924536 -0.63299627   
16     Arabidopsis_thaliana AT1G01160        470.729991  0.12860092   
17     Arabidopsis_thaliana AT1G01170        475.547532 -0.13900212   
18     Arabidopsis_thaliana AT1G01180          7.336174  0.04883864   
19     Arabidopsis_thaliana AT1G01190          7.021378  1.43058217   
20     Arabidopsis_thaliana AT1G01200         20.793513  0.38009601   
21     Arabidopsis_thaliana AT1G01210        276.917283 -0.07026974   
22     Arabidopsis_thaliana AT1G01220        381.341790  0.19073226   
23     Arabidopsis_thaliana AT1G01225         58.051340 -0.10314333   
24     Arabidopsis_thaliana AT1G01230        130.646991 -0.03614923   
25     Arabidopsis_thaliana AT1G01240         75.334935 -0.01087231   
26     Arabidopsis_thaliana AT1G01250          3.988983 -0.11011684   
27     Arabidopsis_thaliana AT1G01260        239.002635  0.18460989   
28     Arabidopsis_thaliana AT1G01280          0.000000          NA   
29     Arabidopsis_thaliana AT1G01290        179.062990  0.03910268   
30     Arabidopsis_thaliana AT1G01300        899.505626 -0.07334544   
⋮      ⋮                    ⋮               ⋮           ⋮             
113910 Zea_mays             ENSRNA049479107   0.0000000          NA   
113911 Zea_mays             ENSRNA049479084   0.0000000          NA   
113912 Zea_mays             Zm00001d000452  159.0286366 -0.01586384   
113913 Zea_mays             ENSRNA049479113   0.0000000          NA   
113914 Zea_mays             ENSRNA049479090   1.4786097 -0.49267831   
113915 Zea_mays             ENSRNA049478841   0.0000000          NA   
113916 Zea_mays             ENSRNA049478799   0.0000000          NA   
113917 Zea_mays             ENSRNA049478848   0.0000000          NA   
113918 Zea_mays             ENSRNA049478830   0.0000000          NA   
113919 Zea_mays             ENSRNA049478872   1.4000538 -3.12786422   
113920 Zea_mays             ENSRNA049478827   1.5825407 -2.41745805   
113921 Zea_mays             ENSRNA049478822   4.7150964 -0.85645241   
113922 Zea_mays             ENSRNA049478869   0.0000000          NA   
113923 Zea_mays             ENSRNA049478813   0.3208452 -2.01170022   
113924 Zea_mays             ENSRNA049478854   0.0000000          NA   
113925 Zea_mays             ENSRNA049478806   0.0000000          NA   
113926 Zea_mays             ENSRNA049478865   0.0000000          NA   
113927 Zea_mays             Zm00001d000455    0.0000000          NA   
113928 Zea_mays             ENSRNA049478560   0.0000000          NA   
113929 Zea_mays             ENSRNA049478557   0.0000000          NA   
113930 Zea_mays             ENSRNA049478534   2.5999914 -0.44166837   
113931 Zea_mays             ENSRNA049478548   0.1077399 -0.76184706   
113932 Zea_mays             ENSRNA049478530   5.8673405 -0.26945237   
113933 Zea_mays             ENSRNA049478543   0.0000000          NA   
113934 Zea_mays             ENS

### load in the rest of the data - hypotheses, trees, fasta and msa for the start 
### + toDo general stats, especially once Orthofinder calculates for HOG)
### +toDo Venn DIagrammes (until 5 species or so then alternative plots)

In [39]:
hypotheses <- read_delim("hypotheses.tsv", delim = "\t")


#create hypotheses object
# each object has list of exp. OGs
#iterate over list of hyptheses and associate expansions, fasta, msa and trees


#first goal - hypothesis object with hypothesis and all exp.HOGs

#could do it over objects in tea directory
#list.files(path = "tea", pattern = "*", full.names=FALSE)


#alternatively via parsing of hyptheses.tsv
hypotheses$hypothesis


## define two classes
# class for the expanded_OG - containing all different types of data we have on it
setClass("expanded_OG", slots=list(genes="spec_tbl_df", 
                                  fasta_files="spec_tbl_df", 
                                  msa="spec_tbl_df", 
                                  tree="spec_tbl_df"))

# class for the hypotheses
setClass("hypothesis", slots=list(description="character", 
                                  number="character",
                                  expanded_in ="character", 
                                  compared_to="character", 
                                  expanded_OGs="list"))




rm(t)
rm(hypothesis_1)
rm(hypothesis_2)


#remove protein_names in the snakemake pipeline - directories clean enough


for (hypothesis in hypotheses$hypothesis) {
    # print(paste0("hypothesis_", hypo))
    
    # create empty list object for hypothesis #
    assign(paste0("hypothesis_", hypothesis), list())

    # assign list of names
    expanded_OGs <- list.files(path = paste0("tea/", hypothesis, "/exp_OGs_proteinnames/"), 
                               pattern = "*", 
                               full.names=FALSE)
    expanded_OGs_short <- str_sub(expanded_OGs, end=-5)


    #create empty list
    t <- list()

    for (exp_OG in expanded_OGs_short) {
    # print(exp_OG)
        test <- new("expanded_OG", 
             genes=read_table(paste0("tea/", hypothesis, "/exp_OGs_proteinnames/", exp_OG, ".txt")), 
             fasta_files=read_table(paste0("tea/", hypothesis, "/fa_records/", exp_OG,".fa")), 
             msa=read_table(paste0("tea/", hypothesis, "/muscle/", exp_OG, ".afa")), 
             tree=read_table(paste0("tea/", hypothesis, "/trees/", exp_OG, ".tree")))
   
        x <- list(test)
        names(x) <- paste0(exp_OG)
        t <- c(t, x)
    }
 
    # create for each hypothesis a complete hypothesis object with correct naming
    # order: hypothesis@info (name, number, expand, compared, exp OGs)$indiv. exp_OGs@objects (exp.OG list, fa, msa, tree)
    # "expanded_in" and "compared_to" are split on ";" in case their size is > 1
    assign(paste0("hypothesis_", hypothesis),
              new("hypothesis", 
                  description=hypotheses$name[hypothesis],
                  number=as.character(hypothesis),
                  expanded_in=unlist(str_split(hypotheses$expanded_in[hypothesis], ";")),
                  compared_to=unlist(str_split(hypotheses$compared_to[hypothesis], ";")), 
                  expanded_OGs=t))
}


# create empty list for final complete hypothesis object

#rm

# create name list of all hypotheses
hypotheses_list <- ls(pattern = "hypothesis_")

# create empty list object to completely hold all hypotheses and associated data
HYPOTHESES.a2tea <- list()

for (hypothesis in hypotheses_list) {
    h <- list(get(hypothesis))
    names(h) <- paste0(hypothesis)
    HYPOTHESES.a2tea <- c(HYPOTHESES.a2tea, h)
}

rm(hypothesis_1)
rm(hypothesis_2)


# final object is called:
# HYPOTHESES.a2tea


#add expanded OGs as column
#    add_column(get(paste0("hypothesis_", hypo)), expanded_OGs)
#class(hypothesis_1@expanded_OGs) <- c("expanded_OG", class(hypothesis_1@expanded_OGs))


Parsed with column specification:
cols(
  hypothesis = col_double(),
  name = col_character(),
  expanded_in = col_character(),
  compared_to = col_character()
)



[1] 1 2

Warning message in rm(hypothesis_1):
“object 'hypothesis_1' not found”
Warning message in rm(hypothesis_2):
“object 'hypothesis_2' not found”
Parsed with column specification:
cols(
  AT5G38810 = col_character()
)

Parsed with column specification:
cols(
  `>HORVU7Hr1G030130` = col_character()
)

Parsed with column specification:
cols(
  `>HORVU7Hr1G030130` = col_character()
)

Parsed with column specification:
cols(
  `((AT2G31470:0.493640954,(AT3G23960:0.636533590,(AT2G19630:0.576423177,AT5G65850:0.517682795)0.209:0.083367155)0.877:0.085148131)0.934:0.109998102,((AT1G53790:0.839517459,AT1G53360:0.781806500)0.896:0.120832922,(AT1G53550:0.479625968,(AT1G61060:0.578846491,AT1G53815:0.453734501)0.850:0.124654668)1.000:0.441383373)0.932:0.125114650,((((((AT2G23160:0.381061611,(AT2G02660:0.236323014,(AT2G16220:0.322212261,(AT2G16450:0.119006021,AT2G15640:0.129680055)0.838:0.041381729)0.938:0.061564770)0.961:0.135482202)1.000:0.414486412,((AT3G57590:0.222616338,(AT3G57580:0.157812134,AT3G56

Parsed with column specification:
cols(
  AT4G16015 = col_character()
)

Parsed with column specification:
cols(
  `>AT5G59920` = col_character()
)

Parsed with column specification:
cols(
  `>AT4G13992` = col_character()
)

Parsed with column specification:
cols(
  `((AT1G69150:0.650429699,(AT4G02190:0.210627098,((AT4G11390:0.187854706,AT4G11550:0.172223509)0.994:0.080903665,(AT4G01760:0.190083156,(AT4G09690:0.435014185,(AT4G02180:0.163612519,(AT4G01740:0.171531439,AT4G01930:0.167365962)0.954:0.044004571)0.932:0.050903645)0.631:0.016192473)0.675:0.023894893)0.594:0.029672428)1.000:0.247705602)1.000:0.230577912,(AT3G46800:0.601289099,((AT5G59920:0.437187556,AT5G22355:0.364454181)0.827:0.060637365,(AT3G48400:0.416141572,AT3G45840:0.524433199)0.259:0.044740124)0.998:0.193811447)0.992:0.160436482,((AT5G40320:0.652816062,((AT2G43220:0.821501041,(AT4G14980:0.511965301,(AT5G45730:0.216517761,(AT3G06990:0.111597681,AT3G07000:0.162138888)1.000:0.229235309)1.000:0.295943527)1.000:0.230617123)0.

Parsed with column specification:
cols(
  AT3G58420 = col_character()
)

Parsed with column specification:
cols(
  `>Zm00001d043312` = col_character()
)

Parsed with column specification:
cols(
  `>Zm00001d043312` = col_character()
)

Parsed with column specification:
cols(
  `(HORVU5Hr1G031980:0.035603864,(Zm00001d023640:0.026335373,Zm00001d041035:0.038709010)1.000:0.035039461,(HORVU4Hr1G034950:0.133775398,((AT5G06600:0.037402160,AT3G11910:0.053918628)1.000:0.085621393,((Zm00001d043312:0.277887785,(((((AT2G05400:0.185869433,(AT2G05420:0.256456199,AT2G05410:0.204041081)0.665:0.025618022)1.000:0.167167166,((AT3G58250:0.305321898,AT3G58270:0.284673207)0.066:0.059841642,(AT3G58400:0.364209513,AT3G58360:0.223561483)0.957:0.108058658)0.594:0.033974641)0.786:0.017411630,(AT3G58370:0.346490993,((AT3G58430:0.563618617,(AT3G58340:0.284880788,AT3G58410:0.284425878)0.187:0.028272269)0.994:0.114647059,((AT3G44805:0.330754769,AT3G44800:0.172267265)0.998:0.265106485,(AT3G58210:0.292689206,AT3G58200:

...

Parsed with column specification:
cols(
  HORVU3Hr1G079670 = col_character()
)

Parsed with column specification:
cols(
  `>HORVU6Hr1G026610` = col_character()
)

Parsed with column specification:
cols(
  `>Zm00001d050336` = col_character()
)

Parsed with column specification:
cols(
  `(HORVU1Hr1G001990:0.132204200,HORVU6Hr1G026610:0.079371731,(Zm00001d050336:0.463902375,HORVU3Hr1G079670:0.058538967)0.833:0.050123060);` = col_character()
)

Parsed with column specification:
cols(
  HORVU1Hr1G040970 = col_character()
)

Parsed with column specification:
cols(
  `>HORVU7Hr1G107520` = col_character()
)

Parsed with column specification:
cols(
  `>Zm00001d037069` = col_character()
)

Parsed with column specification:
cols(
  `(HORVU6Hr1G042040:0.072950607,HORVU1Hr1G015670:0.021618020,(HORVU1Hr1G040970:0.056198293,(HORVU7Hr1G107520:0.054111080,(Zm00001d036620:0.138090909,(Zm00001d037069:2.786240439,(HORVU7Hr1G059320:0.468964889,((HORVU4Hr1G070330:0.038256394,Zm00001d028109:0.098963070)1.000

Parsed with column specification:
cols(
  HORVU1Hr1G016840 = col_character()
)

Parsed with column specification:
cols(
  `>HORVU0Hr1G037830` = col_character()
)

Parsed with column specification:
cols(
  `>HORVU4Hr1G016940` = col_character()
)

Parsed with column specification:
cols(
  `((((Zm00001d032406:0.671585682,(Zm00001d047064:0.730938431,(HORVU4Hr1G072190:0.392963715,(HORVU1Hr1G022630:5.989267893,(Zm00001d048413:0.192201127,Zm00001d027710:0.128591930)0.857:0.271523724)0.000:0.000000010)1.000:0.686753769)0.480:0.079838157)0.708:0.059904206,(HORVU7Hr1G083550:1.068710497,((HORVU5Hr1G097270:1.754960051,HORVU4Hr1G084910:0.576783914)0.848:0.228485462,(HORVU4Hr1G016940:2.266944614,HORVU4Hr1G084920:1.066610050)0.922:0.493372235)0.504:0.175116926)1.000:0.641935696)0.209:0.050114405,Zm00001d035336:0.922228561)0.378:0.046653076,((((HORVU2Hr1G111610:0.535666597,(Zm00001d014603:0.310802421,(Zm00001d014602:0.185599802,Zm00001d014601:0.006935808)0.998:0.265465315)0.998:0.312896725)0.909:0.146

Parsed with column specification:
cols(
  HORVU1Hr1G033990 = col_character()
)

Parsed with column specification:
cols(
  `>HORVU2Hr1G040020` = col_character()
)

Parsed with column specification:
cols(
  `>Zm00001d006607` = col_character()
)

Parsed with column specification:
cols(
  `(Zm00001d006607:0.020885530,Zm00001d021806:0.023033811,(HORVU1Hr1G033990:0.000000005,(HORVU1Hr1G028090:0.000000005,(HORVU4Hr1G022040:0.000000005,HORVU2Hr1G040020:0.000000005)0.000:0.005559195)0.000:0.009869098)0.920:0.091979552);` = col_character()
)

Parsed with column specification:
cols(
  HORVU1Hr1G007100 = col_character()
)

Parsed with column specification:
cols(
  `>HORVU5Hr1G023520` = col_character()
)

Parsed with column specification:
cols(
  `>Zm00001d033314` = col_character()
)

Parsed with column specification:
cols(
  `(HORVU5Hr1G023520:0.506014424,(HORVU4Hr1G014300:0.499811460,(HORVU1Hr1G007100:0.044199229,(HORVU1Hr1G007010:0.069641426,HORVU1Hr1G007040:0.062747518)0.749:0.113154090)1.000:1

Parsed with column specification:
cols(
  HORVU3Hr1G032260 = col_character()
)

Parsed with column specification:
cols(
  `>HORVU0Hr1G032890` = col_character()
)

Parsed with column specification:
cols(
  `>HORVU2Hr1G093690` = col_character()
)

Parsed with column specification:
cols(
  `(((Zm00001d032886:0.135708296,(Zm00001d032882:0.170300003,(Zm00001d032883:0.097048199,(Zm00001d032885:0.012402307,Zm00001d032884:0.024891282)0.959:0.078091983)0.982:0.092484660)0.894:0.064688839)0.997:0.155762592,((Zm00001d032876:0.232700290,(Zm00001d027718:0.264413088,HORVU4Hr1G072400:0.206835301)0.864:0.073615926)0.987:0.146157059,(Zm00001d027717:0.395074285,((((((((Zm00001d038476:0.062957828,((HORVU3Hr1G081230:0.055603944,(HORVU3Hr1G075210:0.000000005,HORVU3Hr1G081180:0.000000005)0.794:0.023029701)1.000:0.264977774,(HORVU1Hr1G069830:1.007543554,Zm00001d043047:0.039253369)0.152:0.004813682)0.823:0.065076103)0.894:0.075902539,HORVU2Hr1G093690:0.915387784)0.000:0.027700023,((HORVU5Hr1G113580:0.10178212

Parsed with column specification:
cols(
  HORVU3Hr1G027570 = col_character()
)

Parsed with column specification:
cols(
  `>HORVU5Hr1G065050` = col_character()
)

Parsed with column specification:
cols(
  `>HORVU1Hr1G003030` = col_character()
)

Parsed with column specification:
cols(
  `((HORVU6Hr1G049390:0.0,AGP50780:0.0):0.000000005,HORVU5Hr1G065050:0.010330075,((HORVU1Hr1G003030:0.695317488,HORVU3Hr1G027570:0.359869867)0.880:0.276245916,(HORVU3Hr1G004410:0.478851875,ZemaCp048:0.010518033)0.702:0.012452150)0.169:0.000000005);` = col_character()
)

Parsed with column specification:
cols(
  HORVU4Hr1G078880 = col_character()
)

Parsed with column specification:
cols(
  `>HORVU0Hr1G014300` = col_character()
)

Parsed with column specification:
cols(
  `>HORVU2Hr1G044230` = col_character()
)

Parsed with column specification:
cols(
  `(((HORVU3Hr1G057780:3.099618274,(Zm00001d035154:2.778829794,(Zm00001d016354:1.349909892,Zm00001d039459:1.386406069)0.924:0.487786917)0.836:0.286281601)0.0

In [37]:
ls()
# remove unnecessary objects to save space
#write to RDS - is there sth. better?

[1] "Arabidopsis_thaliana"                  
 [2] "Arabidopsis_thaliana_DEresultsTable"   
 [3] "combined_AllSpeciesDEResultsDataFrames"
 [4] "dea_list"                              
 [5] "dea_list_short"                        
 [6] "df_with_genes"                         
 [7] "exp_OG"                                
 [8] "expanded_OGs"                          
 [9] "expanded_OGs_short"                    
[10] "gene"                                  
[11] "h"                                     
[12] "HOG_DE_df"                             
[13] "HOG_file_long"                         
[14] "HOG_file_merged"                       
[15] "HOG_file_raw"                          
[16] "HOG_file_short"                        
[17] "Hordeum_vulgare"                       
[18] "Hordeum_vulgare_DEresultsTable"        
[19] "hypotheses"                            
[20] "hypotheses_list"                       
[21] "hypotheses.a2tea"                      
[22] "hypothesis"                            
[23] "i"                                     
[24] "list_AllSpeciesDEResultsDataFrames"    
[25] "species"                               
[26] "species_list"                          
[27] "t"                                     
[28] "test"                                  
[29] "x"                                     
[30] "Zea_mays"                              
[31] "Zea_mays_DEresultsTable"

In [ ]:
#for msa -also install of packages!
readAAMultipleAlignment